# ML Experiment

## Import Libraries

In [1]:
# import libraries
import numpy as np
import pandas as pd
from tqdm import tqdm
from collections import Counter

import sklearn
from sklearn.model_selection import train_test_split, KFold
from sklearn.linear_model import Ridge, LinearRegression
from sklearn.svm import SVR
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import AdaBoostRegressor
from sklearn.neural_network import MLPRegressor
from sklearn.metrics import f1_score, precision_score, recall_score, roc_auc_score, mean_squared_error, mean_absolute_error

from catboost import CatBoostRegressor

import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
import torch.nn.functional as F
import torch.optim as optim

from transformers import BertTokenizerFast, BertModel


# 导入其他文件
from extract_features import load_features, load_features_by_name
from models import BioNN, BioDeepNN, BioResNet
from Model_Training import PeptidesDataLoader

# constant
SAVE = True
device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")

## Model Conparation

In [4]:
# 处理数据
# import data and preprocess
data = pd.read_csv("./Data/processed_peptides10.csv")  # load data

# 得到氨基酸序列
peptides = data.iloc[:, 0].values.tolist()  # 肽链的列表（字符串）

# load extracted features
used_features = ["aac", "knn", "binary"]
features_x = load_features_by_name(used_features).iloc[:, 1:].values

# 处理mmp y的数据
all_mmp_y = data.iloc[:, 1:].values
regular_coefficient = np.max(np.abs(all_mmp_y))
all_mmp_y = all_mmp_y / regular_coefficient

### 常规模型

In [3]:
# 定义验证模型效果的函数
def validate(model: object, x: np.array, y: np.array):
    # 用5折交叉验证来验证模型效果
    kf = KFold(n_splits=5, random_state=33, shuffle=True)
    rg_errors = np.zeros((5, y.shape[1], 3))
    cl_errors = np.zeros((5, y.shape[1], 4))  # 评价指标包括auc, f1, precision, recall
    for i, (train_id, test_id) in tqdm(enumerate(kf.split(x)), desc="Testing on all MMPs", total=5):
        for mmp_i in range(y.shape[1]):
            train_x, train_y = x[train_id], y[:, mmp_i][train_id]
            test_x, test_y = x[test_id], y[:, mmp_i][test_id]

            model.fit(train_x, train_y)
            pred = model.predict(test_x)
            test_y = test_y * regular_coefficient
            pred = pred * regular_coefficient
            # 记录regression error
            mse = mean_squared_error(test_y, pred)
            mae = mean_absolute_error(test_y, pred)
            rmse = np.sqrt(mse)
            rg_errors[i, mmp_i, 0] = mse
            rg_errors[i, mmp_i, 1] = mae
            rg_errors[i, mmp_i, 2] = rmse
            
            # 记录classification error
            cl_pred = pred > 1.65
            cl_test_y = test_y > 1.65
            auc = roc_auc_score(cl_test_y, cl_pred)
            f1 = f1_score(cl_test_y, cl_pred)
            precision = precision_score(cl_test_y, cl_pred)
            recall = recall_score(cl_test_y, cl_pred)
            cl_errors[i, mmp_i, 0] = auc
            cl_errors[i, mmp_i, 1] = f1
            cl_errors[i, mmp_i, 2] = precision
            cl_errors[i, mmp_i, 3] = recall
    return rg_errors, cl_errors

In [ ]:
# linear regression
lr_model = LinearRegression()
lr_rg_error, lr_cl_error = validate(lr_model, features_x, all_mmp_y)
np.save("./Result/lr_rg_error.npy", lr_rg_error)
np.save("./Result/lr_cl_error.npy", lr_cl_error)

In [ ]:
"""
linear regression
aac, knn: [0.5802661 , 0.59635646, 0.76035259]
binary, aac, knn: [0.53352195, 0.56978833, 0.72851419]
"""

In [5]:
# DTR
dtr_model = DecisionTreeRegressor(criterion="squared_error", max_depth=10)
dtr_rg_error, dtr_cl_error = validate(dtr_model, features_x, all_mmp_y)
np.save("./Result/dtr_rg_error.npy", dtr_rg_error)
np.save("./Result/dtr_cl_error.npy", dtr_cl_error)

Testing on all MMPs: 100%|██████████| 5/5 [04:43<00:00, 56.64s/it]


In [7]:
# Adaboost
ada_model = AdaBoostRegressor(n_estimators=100)
ada_rg_error, ada_cl_error = validate(ada_model, features_x, all_mmp_y)
np.save("./Result/ada_rg_error.npy", ada_rg_error)
np.save("./Result/ada_cl_error.npy", ada_cl_error)

NameError: name 'AdaBoostRegressor' is not defined

In [6]:
# Catboost
cat_model = CatBoostRegressor(iterations=1000, depth=10, learning_rate=0.1, loss_function="RMSE")
cat_rg_error, cat_cl_error = validate(cat_model, features_x, all_mmp_y)
np.save("./Result/cat_rg_error.npy", cat_rg_error)
np.save("./Result/cat_cl_error.npy", cat_cl_error)

Testing on all MMPs:   0%|          | 0/5 [00:00<?, ?it/s]

0:	learn: 0.1396313	total: 217ms	remaining: 3m 36s
1:	learn: 0.1341255	total: 285ms	remaining: 2m 22s
2:	learn: 0.1295223	total: 354ms	remaining: 1m 57s
3:	learn: 0.1253348	total: 429ms	remaining: 1m 46s
4:	learn: 0.1215215	total: 509ms	remaining: 1m 41s
5:	learn: 0.1183848	total: 581ms	remaining: 1m 36s
6:	learn: 0.1155728	total: 659ms	remaining: 1m 33s
7:	learn: 0.1134302	total: 738ms	remaining: 1m 31s
8:	learn: 0.1112632	total: 819ms	remaining: 1m 30s
9:	learn: 0.1094957	total: 891ms	remaining: 1m 28s
10:	learn: 0.1078355	total: 963ms	remaining: 1m 26s
11:	learn: 0.1063158	total: 1.04s	remaining: 1m 25s
12:	learn: 0.1048409	total: 1.11s	remaining: 1m 24s
13:	learn: 0.1038546	total: 1.18s	remaining: 1m 23s
14:	learn: 0.1028018	total: 1.25s	remaining: 1m 22s
15:	learn: 0.1018355	total: 1.32s	remaining: 1m 21s
16:	learn: 0.1010878	total: 1.39s	remaining: 1m 20s
17:	learn: 0.1003729	total: 1.47s	remaining: 1m 20s
18:	learn: 0.0996367	total: 1.55s	remaining: 1m 19s
19:	learn: 0.0989878	t

Testing on all MMPs:  20%|██        | 1/5 [34:59<2:19:59, 2099.86s/it]

0:	learn: 0.1401976	total: 104ms	remaining: 1m 44s
1:	learn: 0.1344572	total: 211ms	remaining: 1m 45s
2:	learn: 0.1299272	total: 318ms	remaining: 1m 45s
3:	learn: 0.1258814	total: 424ms	remaining: 1m 45s
4:	learn: 0.1224763	total: 529ms	remaining: 1m 45s
5:	learn: 0.1190621	total: 634ms	remaining: 1m 45s
6:	learn: 0.1161002	total: 753ms	remaining: 1m 46s
7:	learn: 0.1138533	total: 871ms	remaining: 1m 47s
8:	learn: 0.1115937	total: 1.01s	remaining: 1m 50s
9:	learn: 0.1097913	total: 1.11s	remaining: 1m 50s
10:	learn: 0.1081430	total: 1.23s	remaining: 1m 50s
11:	learn: 0.1066903	total: 1.34s	remaining: 1m 50s
12:	learn: 0.1052369	total: 1.46s	remaining: 1m 50s
13:	learn: 0.1041922	total: 1.58s	remaining: 1m 51s
14:	learn: 0.1030629	total: 1.69s	remaining: 1m 50s
15:	learn: 0.1019145	total: 1.8s	remaining: 1m 50s
16:	learn: 0.1009224	total: 1.92s	remaining: 1m 51s
17:	learn: 0.1001191	total: 2.04s	remaining: 1m 51s
18:	learn: 0.0993428	total: 2.15s	remaining: 1m 50s
19:	learn: 0.0986534	to

Testing on all MMPs:  40%|████      | 2/5 [1:13:32<1:51:14, 2224.92s/it]

...

Testing on all MMPs:  80%|████████  | 4/5 [2:33:35<39:06, 2346.93s/it]  

0:	learn: 0.1387125	total: 117ms	remaining: 1m 56s
1:	learn: 0.1331924	total: 236ms	remaining: 1m 57s
2:	learn: 0.1287339	total: 362ms	remaining: 2m
3:	learn: 0.1247735	total: 486ms	remaining: 2m
4:	learn: 0.1209392	total: 612ms	remaining: 2m 1s
5:	learn: 0.1180083	total: 732ms	remaining: 2m 1s
6:	learn: 0.1154517	total: 853ms	remaining: 2m
7:	learn: 0.1129552	total: 975ms	remaining: 2m
8:	learn: 0.1108175	total: 1.1s	remaining: 2m 1s
9:	learn: 0.1090164	total: 1.22s	remaining: 2m 1s
10:	learn: 0.1074637	total: 1.35s	remaining: 2m 1s
11:	learn: 0.1059218	total: 1.48s	remaining: 2m 1s
12:	learn: 0.1046527	total: 1.61s	remaining: 2m 2s
13:	learn: 0.1036730	total: 1.72s	remaining: 2m 1s
14:	learn: 0.1026332	total: 1.84s	remaining: 2m 1s
15:	learn: 0.1015439	total: 1.97s	remaining: 2m
16:	learn: 0.1004849	total: 2.09s	remaining: 2m 1s
17:	learn: 0.0997467	total: 2.21s	remaining: 2m
18:	learn: 0.0988844	total: 2.34s	remaining: 2m
19:	learn: 0.0983105	total: 2.47s	remaining: 2m
20:	learn: 0.

c:\Users\Hongyi LAN\miniconda3\envs\dsl_project\lib\site-packages\sklearn\metrics\_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


0:	learn: 0.1424661	total: 113ms	remaining: 1m 52s
1:	learn: 0.1386340	total: 224ms	remaining: 1m 51s
2:	learn: 0.1356009	total: 335ms	remaining: 1m 51s
3:	learn: 0.1325793	total: 443ms	remaining: 1m 50s
4:	learn: 0.1299549	total: 555ms	remaining: 1m 50s
5:	learn: 0.1278149	total: 673ms	remaining: 1m 51s
6:	learn: 0.1258465	total: 788ms	remaining: 1m 51s
7:	learn: 0.1242519	total: 910ms	remaining: 1m 52s
8:	learn: 0.1227915	total: 1.03s	remaining: 1m 53s
9:	learn: 0.1216130	total: 1.15s	remaining: 1m 54s
10:	learn: 0.1202784	total: 1.27s	remaining: 1m 54s
11:	learn: 0.1190177	total: 1.4s	remaining: 1m 55s
12:	learn: 0.1180318	total: 1.52s	remaining: 1m 55s
13:	learn: 0.1170891	total: 1.64s	remaining: 1m 55s
14:	learn: 0.1163524	total: 1.76s	remaining: 1m 55s
15:	learn: 0.1155810	total: 1.89s	remaining: 1m 56s
16:	learn: 0.1149049	total: 2.02s	remaining: 1m 56s
17:	learn: 0.1143353	total: 2.14s	remaining: 1m 56s
18:	learn: 0.1136386	total: 2.25s	remaining: 1m 56s
19:	learn: 0.1130857	to

Testing on all MMPs: 100%|██████████| 5/5 [3:16:15<00:00, 2355.15s/it]


In [6]:
# MLP
mlp_model = MLPRegressor(hidden_layer_sizes=(256,), activation="relu", max_iter=100)
mlp_rg_error, mlp_cl_error = validate(mlp_model, features_x, all_mmp_y)
np.save("./Result/mlp_rg_error.npy", mlp_rg_error)
np.save("./Result/mlp_cl_error.npy", mlp_cl_error)

Testing on all MMPs:   0%|          | 0/5 [00:00<?, ?it/s]c:\Users\Hongyi LAN\anaconda3\envs\dsl_project\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:698: UserWarning: Training interrupted by user.
  warnings.warn("Training interrupted by user.")


In [4]:
# Neural Network
class NN(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(NN, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.dropout1 = nn.Dropout(0.5)
        self.fc2 = nn.Linear(hidden_size, hidden_size)
        self.dropout2 = nn.Dropout(0.5)
        self.fc3 = nn.Linear(hidden_size, output_size)
        self.device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
    
    def forward(self, x):
        output = F.relu(self.fc1(x))
        output = self.dropout1(output)
        output = F.relu(self.fc2(output))
        output = self.dropout2(output)
        output = F.tanh(self.fc3(output))
        return output
    
    def fit(self, x: np.array, y: np.array):
        self.to(device)
        self.train()
        x = torch.from_numpy(x).float()
        y = torch.from_numpy(y).float()
        dataloader = PeptidesDataLoader([0] * x.shape[0], x, y, batch_size=1024, shuffle=True)
        optimizer = optim.Adam(self.parameters(), lr=0.001)
        criterion = nn.MSELoss()
        for i in range(100):
            for epoch_peptides, epoch_x, epoch_y in dataloader:
                optimizer.zero_grad()
                epoch_x, epoch_y = epoch_x.to(self.device), epoch_y.to(self.device)
                output = self.forward(epoch_x)
                loss = criterion(output, epoch_y)
                loss.backward()
                optimizer.step()
        return
        
    def predict(self, x):
        self.to(device)
        self.eval()
        x = torch.from_numpy(x).float()
        dataloader = PeptidesDataLoader([0] * x.shape[0], x, np.zeros_like(x), batch_size=8192, shuffle=False)
        pred = []
        with torch.no_grad():
            for _, epoch_x, _ in dataloader:
                epoch_x = epoch_x.to(self.device)
                output = self(epoch_x)
                pred.append(output.to("cpu").detach().numpy())
        pred = np.concatenate(pred, axis=0)
        return pred

# NN
kf = KFold(n_splits=5, random_state=33, shuffle=True)
nn_rg_error = np.zeros((5, all_mmp_y.shape[1], 3))
nn_cl_error = np.zeros((5, all_mmp_y.shape[1], 4))  # 评价指标包括auc, f1, precision, recall
for i, (train_id, test_id) in tqdm(enumerate(kf.split(features_x)), desc="Testing on all MMPs", total=5):
    nn_model = NN(features_x.shape[1], 256, all_mmp_y.shape[1])
    train_x, train_y = features_x[train_id], all_mmp_y[train_id]
    test_x, test_y = features_x[test_id], all_mmp_y[test_id]
    nn_model.fit(train_x, train_y)
    pred = nn_model.predict(test_x)
    test_y = test_y * regular_coefficient
    pred = pred * regular_coefficient
    # 记录regression error
    for mmp_i in range(all_mmp_y.shape[1]):
        mse = mean_squared_error(test_y[:, mmp_i], pred[:, mmp_i])
        mae = mean_absolute_error(test_y[:, mmp_i], pred[:, mmp_i])
        rmse = np.sqrt(mse)
        nn_rg_error[i, mmp_i, 0] = mse
        nn_rg_error[i, mmp_i, 1] = mae
        nn_rg_error[i, mmp_i, 2] = rmse
    
    # 记录classification error
    cl_pred = pred > 1.65
    cl_test_y = test_y > 1.65
    for mmp_i in range(all_mmp_y.shape[1]):
        auc = roc_auc_score(cl_test_y[:, mmp_i], cl_pred[:, mmp_i])
        f1 = f1_score(cl_test_y[:, mmp_i], cl_pred[:, mmp_i])
        precision = precision_score(cl_test_y[:, mmp_i], cl_pred[:, mmp_i])
        recall = recall_score(cl_test_y[:, mmp_i], cl_pred[:, mmp_i])
        nn_cl_error[i, mmp_i, 0] = auc
        nn_cl_error[i, mmp_i, 1] = f1
        nn_cl_error[i, mmp_i, 2] = precision
        nn_cl_error[i, mmp_i, 3] = recall
np.save("./Result/nn_rg_error.npy", nn_rg_error)
np.save("./Result/nn_cl_error.npy", nn_cl_error)

Testing on all MMPs:  60%|██████    | 3/5 [00:30<00:20, 10.13s/it]c:\Users\Hongyi LAN\anaconda3\envs\dsl_project\lib\site-packages\sklearn\metrics\_classification.py:1509: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))
Testing on all MMPs: 100%|██████████| 5/5 [00:50<00:00, 10.07s/it]
